In [1]:
# 확률적 경사하강법을 이용한 행렬 분해
# 실제 R행렬의 널이 아닌 행렬 값의 위치 인덱스를 추출해 이 인덱스에 있는 실제 R 행렬 값과 분해된 P,Q를 이용해 다시 조합된 예측 행렬의 값의 RMSE값을 반환
from sklearn.metrics import mean_squared_error

def get_rmse(R, P, Q, non_zeros):
    error = 0
    
    # 두 개의 분해된 행렬 P와 Q.T의 내적으로 예측 R 행렬 생성
    full_pred_matrix = np.dot(P, Q.T)
    
    # 실제 R 행렬에서 널이 아닌 값의 위치 인덱스 추출해 실제 R 행렬과 예측 행렬의 RMSE 추출
    x_non_zero_ind = [non_zero[0] for non_zero in non_zeros]
    y_non_zero_ind = [non_zero[1] for non_zero in non_zeros]
    R_non_zeros = R[x_non_zero_ind, y_non_zero_ind]
    full_pred_matrix_non_zeros = full_pred_matrix[x_non_zero_ind, y_non_zero_ind]
    mse = mean_squared_error(R_non_zeros, full_pred_matrix_non_zeros)
    rmse = np.sqrt(mse)
    
    return rmse

In [6]:
# 행렬 분해 로직
# R : 원본 사용자-아이템 행렬, K : 잠재요인의 차원 수 , steps : SGD의 반복 횟수, learning_rate : 학습률, r_lambda : L2 규제 계수
def matrix_factorization(R, K, steps=200, learning_rate = 0.01, r_lambda=0.01):
    num_users, num_items = R.shape
    # P와 Q 매트릭스의 크기를 지정하고 정규 분포를 가진 랜덤한 값으로 입력
    np.random.seed(1)
    P = np.random.normal(scale=1./K, size=(num_users, K))
    Q = np.random.normal(scale=1./K, size=(num_items, K))
    
    prev_rmse = 10000
    break_count = 0
    
    # R >0 인 행 위치, 열 위치, 값을 non_zeros 리스트 객체에 저장
    non_zeros = [ (i, j, R[i,j]) for i in range(num_users) for j in range(num_items) if R[i, j]>0]
    
    #SGD기법으로 P와 Q 매트릭스를 계속 업데이트
    for step in range(steps):
        for i, j, r in non_zeros:
            # 실제값과 예측 값의 차이인 오류 값 구함
            eij = r - np.dot(P[i, :], Q[j, :].T)
            # Regularization을 반영한 SGD 업데이트 공식 적용
            P[i,:] = P[i,:] + learning_rate*(eij*Q[j,:] - r_lambda*P[i,:])
            Q[j,:] = Q[j,:] + learning_rate*(eij*P[i,:] - r_lambda*Q[j,:])
            
            rmse = get_rmse(R,P,Q,non_zeros)
            
            if (step % 10) == 0:
                print("### iteration step :",step, " rmse :",rmse)
        return P,Q

In [7]:
import pandas as pd
import numpy as np

movies = pd.read_csv('./ml-latest-small/movies.csv')
ratings = pd.read_csv('./ml-latest-small/ratings.csv')
ratings = ratings[['userId','movieId','rating']]
ratings_matrix = ratings.pivot_table('rating', index='userId', columns='movieId')

# title 칼럼을 얻기 위해 movies와 조인 수행
rating_movies = pd.merge(ratings, movies, on='movieId')
# title칼럼으로 pivot 수행
ratings_matrix = rating_movies.pivot_table('rating', index='userId', columns='title')

P,Q = matrix_factorization(ratings_matrix.values, K=50, steps=200, learning_rate = 0.01, r_lambda=0.01)
pred_matrix = np.dot(P, Q.T)

### iteration step : 0  rmse : 3.653457190596704
### iteration step : 0  rmse : 3.653457152752282
### iteration step : 0  rmse : 3.653457125536853
### iteration step : 0  rmse : 3.653457077902461
### iteration step : 0  rmse : 3.6534570363951278
### iteration step : 0  rmse : 3.6534570085398768
### iteration step : 0  rmse : 3.6534569970149575
### iteration step : 0  rmse : 3.653456967000257
### iteration step : 0  rmse : 3.6534569426428147
### iteration step : 0  rmse : 3.6534569206178404
### iteration step : 0  rmse : 3.653456867037414
### iteration step : 0  rmse : 3.653456787685173
### iteration step : 0  rmse : 3.6534568067711084
### iteration step : 0  rmse : 3.6534567849372763
### iteration step : 0  rmse : 3.6534567725245615
### iteration step : 0  rmse : 3.653456780726456
### iteration step : 0  rmse : 3.6534567720843922
### iteration step : 0  rmse : 3.6534567728192875
### iteration step : 0  rmse : 3.6534566471107213
### iteration step : 0  rmse : 3.653456595524333
### itera

### iteration step : 0  rmse : 3.6534513337527335
### iteration step : 0  rmse : 3.6534512989959045
### iteration step : 0  rmse : 3.6534512598070874
### iteration step : 0  rmse : 3.65345122484971
### iteration step : 0  rmse : 3.653451176832753
### iteration step : 0  rmse : 3.6534512045185816
### iteration step : 0  rmse : 3.6534511919722856
### iteration step : 0  rmse : 3.6534510942774943
### iteration step : 0  rmse : 3.6534510901769166
### iteration step : 0  rmse : 3.6534511311573654
### iteration step : 0  rmse : 3.6534511046623
### iteration step : 0  rmse : 3.653451106965576
### iteration step : 0  rmse : 3.6534510533304703
### iteration step : 0  rmse : 3.653451016348671
### iteration step : 0  rmse : 3.6534509869344465
### iteration step : 0  rmse : 3.6534510048134616
### iteration step : 0  rmse : 3.653450964225285
### iteration step : 0  rmse : 3.6534509080023705
### iteration step : 0  rmse : 3.6534508304267996
### iteration step : 0  rmse : 3.653450737779276
### iterat

### iteration step : 0  rmse : 3.6534472078556113
### iteration step : 0  rmse : 3.6534472130150535
### iteration step : 0  rmse : 3.6534472057128853
### iteration step : 0  rmse : 3.653447193183169
### iteration step : 0  rmse : 3.653447199012454
### iteration step : 0  rmse : 3.653447202533401
### iteration step : 0  rmse : 3.6534471879857895
### iteration step : 0  rmse : 3.653447171873252
### iteration step : 0  rmse : 3.6534471430904416
### iteration step : 0  rmse : 3.6534471513162754
### iteration step : 0  rmse : 3.653447141925451
### iteration step : 0  rmse : 3.65344713064652
### iteration step : 0  rmse : 3.6534471212063067
### iteration step : 0  rmse : 3.653447080767522
### iteration step : 0  rmse : 3.6534470692877345
### iteration step : 0  rmse : 3.6534470593817563
### iteration step : 0  rmse : 3.653447059219179
### iteration step : 0  rmse : 3.653447013584986
### iteration step : 0  rmse : 3.6534469965137952
### iteration step : 0  rmse : 3.653446972742645
### iterati

### iteration step : 0  rmse : 3.6534433561809903
### iteration step : 0  rmse : 3.6534433384325005
### iteration step : 0  rmse : 3.6534433265248194
### iteration step : 0  rmse : 3.6534432953960243
### iteration step : 0  rmse : 3.653443294197453
### iteration step : 0  rmse : 3.653443298873237
### iteration step : 0  rmse : 3.653443257258936
### iteration step : 0  rmse : 3.6534432474010576
### iteration step : 0  rmse : 3.6534432246573383
### iteration step : 0  rmse : 3.653443177529796
### iteration step : 0  rmse : 3.653443125569857
### iteration step : 0  rmse : 3.6534431383049197
### iteration step : 0  rmse : 3.6534431302610795
### iteration step : 0  rmse : 3.653443118794425
### iteration step : 0  rmse : 3.653443137824376
### iteration step : 0  rmse : 3.6534431310367386
### iteration step : 0  rmse : 3.6534431309529145
### iteration step : 0  rmse : 3.65344313016865
### iteration step : 0  rmse : 3.6534431388651245
### iteration step : 0  rmse : 3.6534431299316728
### itera

### iteration step : 0  rmse : 3.6534407651492113
### iteration step : 0  rmse : 3.6534407688720725
### iteration step : 0  rmse : 3.653440806241744
### iteration step : 0  rmse : 3.6534407957648067
### iteration step : 0  rmse : 3.6534407975818186
### iteration step : 0  rmse : 3.65344080288269
### iteration step : 0  rmse : 3.6534407731325844
### iteration step : 0  rmse : 3.653440719983671
### iteration step : 0  rmse : 3.653440701608636
### iteration step : 0  rmse : 3.65344068797565
### iteration step : 0  rmse : 3.653440676107726
### iteration step : 0  rmse : 3.653440676694338
### iteration step : 0  rmse : 3.653440664563957
### iteration step : 0  rmse : 3.653440660474259
### iteration step : 0  rmse : 3.6534406750114155
### iteration step : 0  rmse : 3.653440647856524
### iteration step : 0  rmse : 3.6534406594161313
### iteration step : 0  rmse : 3.6534406328867384
### iteration step : 0  rmse : 3.6534406198055844
### iteration step : 0  rmse : 3.653440666202426
### iteration

...

### iteration step : 0  rmse : 2.910669996159183
### iteration step : 0  rmse : 2.9106698670018605
### iteration step : 0  rmse : 2.9106528240064007
### iteration step : 0  rmse : 2.910632393427943
### iteration step : 0  rmse : 2.9106305924216773
### iteration step : 0  rmse : 2.9105681667826175
### iteration step : 0  rmse : 2.910528015400831
### iteration step : 0  rmse : 2.910525656294819
### iteration step : 0  rmse : 2.9104781158562716
### iteration step : 0  rmse : 2.910464636868401
### iteration step : 0  rmse : 2.910408199951082
### iteration step : 0  rmse : 2.9103719374079433
### iteration step : 0  rmse : 2.910366528219925
### iteration step : 0  rmse : 2.910364527630193
### iteration step : 0  rmse : 2.9103638453185754
### iteration step : 0  rmse : 2.910363024817879
### iteration step : 0  rmse : 2.910315195724012
### iteration step : 0  rmse : 2.9102623511945676
### iteration step : 0  rmse : 2.9102349734383153
### iteration step : 0  rmse : 2.9102011935353684
### iterat

### iteration step : 0  rmse : 2.9066248853285495
### iteration step : 0  rmse : 2.906578856691751
### iteration step : 0  rmse : 2.9066031250561966
### iteration step : 0  rmse : 2.906631789647952
### iteration step : 0  rmse : 2.906659487676416
### iteration step : 0  rmse : 2.9066585748836604
### iteration step : 0  rmse : 2.9066479659757936
### iteration step : 0  rmse : 2.906637397380087
### iteration step : 0  rmse : 2.9066191744473877
### iteration step : 0  rmse : 2.9066329827075736
### iteration step : 0  rmse : 2.906624768361367
### iteration step : 0  rmse : 2.906633739532142
### iteration step : 0  rmse : 2.906612003515288
### iteration step : 0  rmse : 2.906632230589378
### iteration step : 0  rmse : 2.9066097759547946
### iteration step : 0  rmse : 2.9065742232685534
### iteration step : 0  rmse : 2.906516344265341
### iteration step : 0  rmse : 2.9064917612062984
### iteration step : 0  rmse : 2.9064753585428713
### iteration step : 0  rmse : 2.906449200619619
### iterat

### iteration step : 0  rmse : 2.9047626231896744
### iteration step : 0  rmse : 2.9047539150840413
### iteration step : 0  rmse : 2.9047288872642665
### iteration step : 0  rmse : 2.9047206646859767
### iteration step : 0  rmse : 2.9047549815029274
### iteration step : 0  rmse : 2.9047207429046673
### iteration step : 0  rmse : 2.904702215344692
### iteration step : 0  rmse : 2.9046849066099796
### iteration step : 0  rmse : 2.9046746563627117
### iteration step : 0  rmse : 2.904651246706049
### iteration step : 0  rmse : 2.904699354651163
### iteration step : 0  rmse : 2.90469673397463
### iteration step : 0  rmse : 2.9046640396231145
### iteration step : 0  rmse : 2.9046567855779037
### iteration step : 0  rmse : 2.9046490662107196
### iteration step : 0  rmse : 2.9046342546135966
### iteration step : 0  rmse : 2.9046266682774675
### iteration step : 0  rmse : 2.9046238074211383
### iteration step : 0  rmse : 2.9046148721770506
### iteration step : 0  rmse : 2.904598298941906
### it

### iteration step : 0  rmse : 2.903834979323976
### iteration step : 0  rmse : 2.9038477286797635
### iteration step : 0  rmse : 2.9038437324659037
### iteration step : 0  rmse : 2.9038507787687045
### iteration step : 0  rmse : 2.9038335046574657
### iteration step : 0  rmse : 2.903817576119207
### iteration step : 0  rmse : 2.903799718893324
### iteration step : 0  rmse : 2.9038013273001586
### iteration step : 0  rmse : 2.903805099222534
### iteration step : 0  rmse : 2.903794715837916
### iteration step : 0  rmse : 2.903789041513749
### iteration step : 0  rmse : 2.903817366893963
### iteration step : 0  rmse : 2.903810780666551
### iteration step : 0  rmse : 2.9037925910155504
### iteration step : 0  rmse : 2.9037855981540632
### iteration step : 0  rmse : 2.903776397934033
### iteration step : 0  rmse : 2.9037503877829027
### iteration step : 0  rmse : 2.903742843999936
### iteration step : 0  rmse : 2.9037327590163655
### iteration step : 0  rmse : 2.903719841196196
### iterati

### iteration step : 0  rmse : 2.902714252985733
### iteration step : 0  rmse : 2.9027263025567547
### iteration step : 0  rmse : 2.9027288619797287
### iteration step : 0  rmse : 2.902721003412517
### iteration step : 0  rmse : 2.9027134209813226
### iteration step : 0  rmse : 2.9026954834736913
### iteration step : 0  rmse : 2.9026874651728907
### iteration step : 0  rmse : 2.9026775196714163
### iteration step : 0  rmse : 2.902663463797258
### iteration step : 0  rmse : 2.9026925447679264
### iteration step : 0  rmse : 2.9026928739186886
### iteration step : 0  rmse : 2.9026830554714707
### iteration step : 0  rmse : 2.9026783827415112
### iteration step : 0  rmse : 2.9027207329467415
### iteration step : 0  rmse : 2.90274206352596
### iteration step : 0  rmse : 2.9027334242205067
### iteration step : 0  rmse : 2.9027235328642735
### iteration step : 0  rmse : 2.902711700420508
### iteration step : 0  rmse : 2.902703636625145
### iteration step : 0  rmse : 2.902694341582641
### iter

In [9]:
ratings_pred_matrix = pd.DataFrame(data=pred_matrix, index = ratings_matrix.index, columns = ratings_matrix.columns)
ratings_pred_matrix.head(3)

title   '71 (2014)  'Hellboy': The Seeds of Creation (2004)  \
userId                                                        
1        -0.004665                                 0.002968   
2         0.003446                                -0.003573   
3        -0.002569                                -0.004912   

title   'Round Midnight (1986)  'Salem's Lot (2004)  \
userId                                                
1                     0.000006            -0.001428   
2                    -0.000636            -0.001340   
3                    -0.006891            -0.003441   

title   'Til There Was You (1997)  'Tis the Season for Love (2015)  \
userId                                                               
1                        0.002956                        -0.002909   
2                        0.001394                         0.001902   
3                       -0.001712                         0.003149   

title   'burbs, The (1989)  'night Mother (1986)  (500) Days of Summer (2009)  \
userId                                                                          
1                -0.003659             -0.001387                    -0.003045   
2                -0.004263             -0.001990                     0.000833   
3                 0.000464              0.002608                    -0.000831   

title   *batteries not included (1987)  ...  Zulu (2013)  [REC] (2007)  \
userId                                  ...                              
1                            -0.001356  ...     0.003241      0.033969   
2                            -0.002115  ...    -0.000719      0.018391   
3                            -0.000940  ...    -0.002913     -0.008313   

title   [REC]² (2009)  [REC]³ 3 Génesis (2012)  \
userId                                           
1            0.018578                 0.003456   
2            0.007601                 0.007915   
3           -0.003831                -0.001247   

title   anohana: The Flower We Saw That Day - The Movie (2013)  \
userId                                                           
1                                                0.002014        
2                                                0.003898        
3                                                0.003796        

title   eXistenZ (1999)  xXx (2002)  xXx: State of the Union (2005)  \
userId                                                                
1              0.053826    0.038394                        0.012764   
2              0.029702    0.018317                        0.000816   
3             -0.002812    0.002065                       -0.001586   

title   ¡Three Amigos! (1986)  À nous la liberté (Freedom for Us) (1931)  
userId                                                                    
1                    0.044216                                  -0.002709  
2                    0.022511                                  -0.000307  
3                   -0.003380                                   0.000499  

[3 rows x 9719 columns]

In [12]:
def get_unseen_movies(ratings_matrix, userId):
    # userId로 입력받은 사용자의 모든 영화 정보를 추출해 Series로 반환
    user_rating = ratings_matrix.loc[userId,:]
    
    # 0보다 크면 기존에 관람한 영화
    already_seen = user_rating[user_rating > 0].index.tolist()
    movies_list = ratings_matrix.columns.tolist()
    
    #list comprehension으로 already_seen 영화는 제외
    unseen_list = [movie for movie in movies_list if movie not in already_seen]
    return unseen_list

def recomm_movie_by_userid(pred_df, userId, unseen_list, top_n=10):
    recomm_movies = pred_df.loc[userId, unseen_list].sort_values(ascending=False)[:top_n]
    return recomm_movies

In [13]:
# 사용자가 관람하지 않은 영화명 추출
unseen_list = get_unseen_movies(ratings_matrix, 9)

# 잠재 요인 협업 필터링으로 영화 추천
recomm_movies = recomm_movie_by_userid(ratings_pred_matrix, 9, unseen_list, top_n=10)

# 평점 데이터를 DataFrame으로 생성
recomm_movies = pd.DataFrame(data=recomm_movies.values, index=recomm_movies.index, columns=['pred_score'])
recomm_movies

pred_score
title                                                         
Lord of the Rings: The Return of the King, The ...    0.038016
Shawshank Redemption, The (1994)                      0.037021
Silence of the Lambs, The (1991)                      0.036636
Matrix, The (1999)                                    0.033958
Pulp Fiction (1994)                                   0.033859
Godfather, The (1972)                                 0.033244
Good Will Hunting (1997)                              0.033140
Saving Private Ryan (1998)                            0.032515
Forrest Gump (1994)                                   0.031885
Memento (2000)                                        0.031691